# Web scraping the President's lies in 16 lines of Python

*Created by Kevin Markham of [Data School](http://www.dataschool.io/). Hosted on [GitHub](https://github.com/justmarkham/trump-lies).*

## Summary

This an introductory tutorial on web scraping in Python. All that is required to follow along is a basic understanding of the Python programming language.

By the end of this tutorial, you will be able to scrape data from a static web page using the **requests** and **Beautiful Soup** libraries, and export that data into a structured text file using the **pandas** library.

## Outline

- What is web scraping?
- Examining the New York Times article
    - Examining the HTML
    - Fact 1: HTML consists of tags
    - Fact 2: Tags can have attributes
    - Fact 3: Tags can be nested
- Reading the web page into Python
- Parsing the HTML using Beautiful Soup
    - Collecting all of the records
    - Extracting the date
    - Extracting the lie
    - Extracting the explanation
    - Extracting the URL
    - Recap: Beautiful Soup methods and attributes
- Building the dataset
    - Applying a tabular data structure
    - Exporting the dataset to a CSV file
- Summary: 16 lines of Python code
    - Appendix A: Web scraping advice
    - Appendix B: Web scraping resources
    - Appendix C: Alternative syntax for Beautiful Soup

## What is web scraping?

On July 21, 2017, the New York Times updated an opinion article called [Trump's Lies](https://www.nytimes.com/interactive/2017/06/23/opinion/trumps-lies.html), detailing every public lie the President has told since taking office. Because this is a newspaper, the information was (of course) published as a block of text. This is a great format for human consumption, but it can't easily be understood by a computer. **In this tutorial, we'll extract the President's lies from the New York Times article and store them in a structured dataset.**

This is a common scenario: You find a web page that contains data you want to analyze, but it's not presented in a format that you can easily download and read into your favorite data analysis tool. You might imagine manually copying and pasting the data into a spreadsheet, but in most cases, that is way too time consuming. A technique called **web scraping** is a useful way to automate this process.

What is web scraping? It's the process of extracting information from a web page **by taking advantage of patterns** in the web page's underlying code. Let's start looking for these patterns!

## Examining the New York Times article

Here's the way the article presented the information:

![Screenshot of the article](images/article_1.png)

When converting this into a dataset, **you can think of each lie as a "record" with four fields:**

1. The date of the lie.
2. The lie itself (as a quotation).
3. The writer's brief explanation of why it was a lie.
4. The URL of an article that substantiates the claim that it was a lie.

Importantly, those fields have different formatting, which is consistent throughout the article: the date is bold red text, the lie is "regular" text, the explanation is gray italics text, and the URL is linked from the gray italics text.

**Why does the formatting matter?** Because it's very likely that the code underlying the web page "tags" those fields differently, and we can take advantage of that pattern when scraping the page. Let's take a look at the source code, known as HTML:

1. Name of project
2. Coin of project
4. Number of github commits (**highlited**)
5. URL to github commit insights
6. Slogan of the project
7. Number of contributors
8. Name of top contributor

## Examining the HTML

To view the HTML code that generates a web page, you right click on it and select "View Page Source" in Chrome or Firefox, "View Source" in Internet Explorer, or "Show Page Source" in Safari. (If that option doesn't appear in Safari, just open Safari Preferences, select the Advanced tab, and check "Show Develop menu in menu bar".)

Here are the first few lines you will see if you view the source of the New York Times article:

![Screenshot of the source](images/source_1.png)

Let's locate the **first lie** by searching the HTML for the text "iraq":

![Screenshot of the source](images/source_2.png)

Thankfully, you only have to understand **three basic facts** about HTML in order to get started with web scraping!

## Fact 1: HTML consists of tags

You can see that the HTML contains the article text, along with "tags" (specified using angle brackets) that "mark up" the text. ("HTML" stands for Hyper Text Markup Language.)

For example, one tag is `<strong>`, which means "use bold formatting". There is a `<strong>` tag before "Jan. 21" and a `</strong>` tag after it. The first is an "opening tag" and the second is a "closing tag" (denoted by the `/`), which indicates to the web browser **where to start and stop applying the formatting.** In other words, this tag tells the web browser to make the text "Jan. 21" bold. (Don't worry about the `&nbsp;` - we'll deal with that later.)

## Fact 2: Tags can have attributes

HTML tags can have "attributes", which are specified in the opening tag. For example, `<span class="short-desc">` indicates that this particular `<span>` tag has a `class` attribute with a value of `short-desc`.

For the purpose of web scraping, **you don't actually need to understand** the meaning of `<span>`, `class`, or `short-desc`. Instead, you just need to recognize that tags can have attributes, and that they are specified in this particular way.

## Fact 3: Tags can be nested

Let's pretend my HTML code said:

`Hello <strong><em>Data School</em> students</strong>`

The text **Data School students** would be bold, because all of that text is between the opening `<strong>` tag and the closing `</strong>` tag. The text ***Data School*** would also be in italics, because the `<em>` tag means "use italics". The text "Hello" would not be bold or italics, because it's not within either the `<strong>` or `<em>` tags. Thus, it would appear as follows:

Hello ***Data School* students**

The central point to take away from this example is that **tags "mark up" text from wherever they open to wherever they close,** regardless of whether they are nested within other tags.

Got it? You now know enough about HTML in order to start web scraping!

## Reading the web page into Python

The first thing we need to do is to read the HTML for this article into Python, which we'll do using the [requests](http://docs.python-requests.org/en/master/) library. (If you don't have it, you can `pip install requests` from the command line.)

In [9]:
import requests
r = requests.get('https://www.nytimes.com/interactive/2017/06/23/opinion/trumps-lies.html')

In [1]:
import requests
r = requests.get('https://www.cryptomiso.com/')

In [2]:
print(r.text[0:500])

<!DOCTYPE html>
<html lang="en">

  <head>
	<!-- Global site tag (gtag.js) - Google Analytics -->
	<script async src="https://www.googletagmanager.com/gtag/js?id=UA-194417-4"></script>
	<script>
	  window.dataLayer = window.dataLayer || [];
	  function gtag(){dataLayer.push(arguments);}
	  gtag('js', new Date());
	  gtag('config', 'UA-194417-4');
	</script>
	
	<title>CryptoMiso - Ranking cryptocurrencies based on Github commits of past 12 months</title>
    <meta charset="utf-8">
    <meta name=


The code above fetches our web page from the URL, and stores the result in a "response" object called `r`. That response object has a `text` attribute, which contains the same HTML code we saw when viewing the source from our web browser:

In [10]:
# print the first 500 characters of the HTML
print(r.text[0:500])

<!DOCTYPE html>
<!--[if (gt IE 9)|!(IE)]> <!--><html lang="en" class="no-js page-interactive section-opinion page-theme-standard tone-opinion page-interactive-default limit-small layout-xlarge app-interactive" itemid="https://www.nytimes.com/interactive/2017/06/23/opinion/trumps-lies.html" itemtype="http://schema.org/NewsArticle" itemscope xmlns:og="http://opengraphprotocol.org/schema/"><!--<![endif]-->
<!--[if IE 9]> <html lang="en" class="no-js ie9 lt-ie10 page-interactive section-opinion page


## Parsing the HTML using Beautiful Soup

We're going to parse the HTML using the [Beautiful Soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) library, which is a popular Python library for web scraping. (If you don't have it, you can `pip install beautifulsoup4` from the command line.)

In [3]:
from bs4 import BeautifulSoup
soup = BeautifulSoup(r.text, 'html.parser')

In [4]:
soup

<!DOCTYPE html>

<html lang="en">
<head>
<!-- Global site tag (gtag.js) - Google Analytics -->
<script async="" src="https://www.googletagmanager.com/gtag/js?id=UA-194417-4"></script>
<script>
	  window.dataLayer = window.dataLayer || [];
	  function gtag(){dataLayer.push(arguments);}
	  gtag('js', new Date());
	  gtag('config', 'UA-194417-4');
	</script>
<title>CryptoMiso - Ranking cryptocurrencies based on Github commits of past 12 months</title>
<meta charset="utf-8"/>
<meta content="width=device-width, initial-scale=1, shrink-to-fit=no" name="viewport"/>
<meta content="CryptoMiso is a web service ranking cryptocurrencies based on the commit history of their most popular Github repository." name="description"/>
<meta content="crypto, currency, github, commits, popularity" name="keywords"/>
<meta content="Bart Claeys" name="author"/>
<meta content="CryptoMiso" property="og:site_name">
<meta content="article" property="og:type">
<meta content="https://www.cryptomiso.com/assets/miso_fb

In [20]:
from bs4 import BeautifulSoup
soup = BeautifulSoup(r.text, 'html.parser')

In [5]:
soup.find_all('h4','card-title')

[<h4 class="card-title">
 					1. Insolar · <a href="#INS">INS</a>
 <small class="float-right"><a href="https://github.com/insolar/insolar/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="9,503 commits last 12 months">9,503 commits</span></a><br/><span class="smaller text-muted float-right mt-1">24 contributors</span></small>
 </h4>, <h4 class="card-title">
 					2. 0x · <a href="#ZRX">ZRX</a>
 <small class="float-right"><a href="https://github.com/0xProject/0x.js/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="7,189 commits last 12 months">7,189 commits</span></a><br/><span class="smaller text-muted float-right mt-1">55 contributors</span></small>
 </h4>, <h4 class="card-title">
 					3. Holo · <a href="#HOT">HOT</a>
 <small class="float-right"><a href="https://github.com/holochain/holochain-rust/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="6,712 commits last 12 months">6,712 commits</

In [50]:
soup.find('span', 'smaller text-muted float-right mt-1').text

'24 contributors'

The code above parses the HTML (stored in `r.text`) into a special object called `soup` that the Beautiful Soup library understands. In other words, Beautiful Soup is **reading the HTML and making sense of its structure.**

(Note that `html.parser` is the parser included with the Python standard library, though other parsers can be used by Beautiful Soup. See [differences between parsers](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#differences-between-parsers) to learn more.)

## Collecting all of the records

The Python code above is the standard code I use with every web scraping project. Now, we're going to start **taking advantage of the patterns we noticed in the article formatting** to build our dataset!

Let's take another look at the article, and compare it with the HTML:

![Screenshot of the article](images/article_1.png)

![Screenshot of the source](images/source_3.png)

You might have noticed that each record has the following format:

`<span class="short-desc"><strong> DATE </strong> LIE <span class="short-truth"><a href="URL"> EXPLANATION </a></span></span>`

There's an outer `<span>` tag, and then nested within it is a `<strong>` tag plus another `<span>` tag, which itself contains an `<a>` tag. All of these tags affect the formatting of the text. And because the New York Times wants each record to appear in a consistent way in your web browser, we know that **each record will be tagged in a consistent way in the HTML.** This is the pattern that allows us to build our dataset!

Let's ask Beautiful Soup to **find all of the records:**

```HTML
<h4 class='card-title'>PROJECT NAME <a href='#INS'>COIN</a><small class='float-right'><a href='GIT URL' target='_blank'><span class='badge badge-success' title='9,139 commits last 12 months'>NUMBER OF COMMITS</span></a><br/><span class='smaller text-muted float-right mt-1'>NUMBER OF CONTRIBUTORS</span></small>
</h4>
<h6 class='card-subtitle mb-2 text-muted'>SLOGAN</h6>
```

In [6]:
results = soup.find_all('h4', class_='card-title')

This code searches the `soup` object for all `<span>` tags with the attribute `class="short-desc"`. It returns a special Beautiful Soup object (called a "ResultSet") containing the search results.

`results` acts like a **Python list**, so we can check its length:

In [7]:
len(results)

805

There are 116 results, which seems reasonable given the length of the article. (If this number did not seem reasonable, we would examine the HTML further to determine if our assumptions about the patterns in the HTML were incorrect.)

We can also slice the object like a list, in order to examine the **first three results:**

In [8]:
results[0:3]

[<h4 class="card-title">
 					1. Insolar · <a href="#INS">INS</a>
 <small class="float-right"><a href="https://github.com/insolar/insolar/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="9,503 commits last 12 months">9,503 commits</span></a><br/><span class="smaller text-muted float-right mt-1">24 contributors</span></small>
 </h4>, <h4 class="card-title">
 					2. 0x · <a href="#ZRX">ZRX</a>
 <small class="float-right"><a href="https://github.com/0xProject/0x.js/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="7,189 commits last 12 months">7,189 commits</span></a><br/><span class="smaller text-muted float-right mt-1">55 contributors</span></small>
 </h4>, <h4 class="card-title">
 					3. Holo · <a href="#HOT">HOT</a>
 <small class="float-right"><a href="https://github.com/holochain/holochain-rust/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="6,712 commits last 12 months">6,712 commits</

We'll also check that the **last result** in this object matches the last record in the article:

![Screenshot of the article](images/article_2.png)

In [54]:
results[-1]

<div class="card-body">
<span id="ct_c3XJzIm"></span>
</div>

Looks good!

We have now collected all 116 of the records, but we still need to **separate each record into its four components** (date, lie, explanation, and URL) in order to give the dataset some structure.

## Extracting the date

Web scraping is often an iterative process, in which you experiment with your code until it works exactly as you desire. To simplify the experimentation, we'll start by only working with the **first record** in the `results` object, and then later on we'll modify our code to use a loop:

In [162]:
first_result = results[0]
first_result

<h4 class="card-title">
					1. Insolar · <a href="#INS">INS</a>
<small class="float-right"><a href="https://github.com/insolar/insolar/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="9,482 commits last 12 months">9,482 commits</span></a><br/><span class="smaller text-muted float-right mt-1">24 contributors</span></small>
</h4>

In [163]:
first_result = results[0]
first_result

<h4 class="card-title">
					1. Insolar · <a href="#INS">INS</a>
<small class="float-right"><a href="https://github.com/insolar/insolar/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="9,482 commits last 12 months">9,482 commits</span></a><br/><span class="smaller text-muted float-right mt-1">24 contributors</span></small>
</h4>

Although `first_result` may look like a Python string, you'll notice that there are no quote marks around it. Instead, it's another special Beautiful Soup object (called a "Tag") that has specific methods and attributes.

In order to locate the date, we can use its `find()` method to **find a single tag** that matches a specific pattern, in contrast to the `find_all()` method we used above to **find all tags** that match a pattern:

```HTML
<h4 class='card-title'>PROJECT NAME <a href='#INS'>COIN</a><small class='float-right'><a href='GIT URL' target='_blank'><span class='badge badge-success' title='9,139 commits last 12 months'>NUMBER OF COMMITS</span></a><br/><span class='smaller text-muted float-right mt-1'>NUMBER OF CONTRIBUTORS</span></small>
</h4>
<h6 class='card-subtitle mb-2 text-muted'>SLOGAN</h6>
```

In [56]:
first_result.find('strong')

**Extracting the PROJECT NAME** 

In [166]:
first_result.contents[0][6:][0:-3]

'1. Insolar'

In [183]:
#alternative to above
first_result.contents[0].split()[1]

'Insolar'

**Extracting the COIN**

In [170]:
first_result.a.text

'INS'

**Extracting GIT URL**

In [171]:
first_result.find('small').find('a')['href']

'https://github.com/insolar/insolar/graphs/commit-activity'

**Extracting the NB OF COMMITS** -- need better way re: singular. Transform to int

In [172]:
first_result.find('span').contents[0].split()[0]

'9,482'

In [ ]:
# Not as clean
first_result.find('span').text[0:-8]

**Extracting the NB OF CONTRIBUTORS**

In [174]:
first_result.small.find('span', 'smaller text-muted float-right mt-1').text

'24 contributors'

In [97]:
first_result.h4.find('small')

<small class="float-right"><a href="https://github.com/insolar/insolar/graphs/commit-activity" target="_blank"><span class="badge badge-success" title="9,482 commits last 12 months">9,482 commits</span></a><br/><span class="smaller text-muted float-right mt-1">24 contributors</span></small>

In [172]:
first_result.h4.find('small').find_all('span', class_='smaller text-muted float-right mt-1')

[<span class="smaller text-muted float-right mt-1">23 contributors</span>]

**Extracting the SLOGAN**

In [176]:
first_result.h6.contents[0]

AttributeError: 'NoneType' object has no attribute 'contents'

## Recap: Beautiful Soup methods and attributes

Before we finish building the dataset, I want to summarize a few ways you can interact with Beautiful Soup objects.

You can apply these **two methods** to either the initial `soup` object or a Tag object (such as `first_result`):

- `find()`: searches for the first matching tag, and returns a Tag object
- `find_all()`: searches for all matching tags, and returns a ResultSet object (which you can treat like a list of Tags)

You can extract information from a Tag object (such as `first_result`) using these **two attributes:**

- `text`: extracts the text of a Tag, and returns a string
- `contents`: extracts the children of a Tag, and returns a list of Tags and strings

It's important to keep track of whether you are interacting with a Tag, ResultSet, list, or string, because that affects which methods and attributes you can access.

And of course, there are many more methods and attributes available to you, which are described in the [Beautiful Soup documentation](https://www.crummy.com/software/BeautifulSoup/bs4/doc/).

## Building the dataset

Now that we've figured out how to extract the four components of `first_result`, we can **create a loop to repeat this process** on all 116 `results`. We'll store the output in a **list of tuples** called `records`:

In [184]:
records = []
for result in results:
    name = result.contents[0][6:][0:-3]
    coin = result.a.text
    url = result.find('small').find('a')['href']
    commits = result.find('span').contents[0].split()[0]
    contributors = result.small.find('span', 'smaller text-muted float-right mt-1').text
##    slogan = result.h6.contents
    records.append((name, coin, url, commits, contributors))

Since there were 116 `results`, we should have 116 `records`:

In [185]:
len(records)

804

Let's do a quick spot check of the first three records:

In [186]:
records[0:]

[('1. Insolar',
  'INS',
  'https://github.com/insolar/insolar/graphs/commit-activity',
  '9,482',
  '24 contributors'),
 ('2. 0x',
  'ZRX',
  'https://github.com/0xProject/0x.js/graphs/commit-activity',
  '7,121',
  '55 contributors'),
 ('3. Holo',
  'HOT',
  'https://github.com/holochain/holochain-rust/graphs/commit-activity',
  '6,458',
  '28 contributors'),
 ('4. aelf',
  'ELF',
  'https://github.com/aelfProject/AElf/graphs/commit-activity',
  '5,433',
  '26 contributors'),
 ('5. RChain',
  'RHOC',
  'https://github.com/rchain/rchain/graphs/commit-activity',
  '5,173',
  '49 contributors'),
 ('6. TRON',
  'TRX',
  'https://github.com/tronprotocol/java-tron/graphs/commit-activity',
  '4,747',
  '76 contributors'),
 ('7. TrueChain',
  'TRUE',
  'https://github.com/truechain/truechain-engineering-code/graphs/commit-activity',
  '4,575',
  '33 contributors'),
 ('8. Zeusshield',
  'ZSC',
  'https://github.com/zeus-shield/zsc/graphs/commit-activity',
  '4,451',
  '7 contributors'),
 ('9.

Looks good!

## Applying a tabular data structure

The last major step in this process is to apply a tabular data structure to our existing structure (which is a list of tuples). We're going to do this using the [pandas](http://pandas.pydata.org/) library, an incredibly popular Python library for data analysis and manipulation. (If you don't have it, here are the [installation instructions](http://pandas.pydata.org/pandas-docs/stable/install.html).)

The primary data structure in pandas is the "DataFrame", which is suitable for tabular data with columns of different types, **similar to an Excel spreadsheet or SQL table.** We can convert our list of tuples into a DataFrame by passing it to the DataFrame constructor and specifying the desired column names:

In [187]:
import pandas as pd
df = pd.DataFrame(records, columns=['name', 'coin', 'url', 'commits', 'contributors'])

The DataFrame includes a `head()` method, which allows you to examine the top of the DataFrame:

In [222]:
df.head()

name  coin                                                url  \
0  1. Insolar   INS  https://github.com/insolar/insolar/graphs/comm...   
1       2. 0x   ZRX  https://github.com/0xProject/0x.js/graphs/comm...   
2     3. Holo   HOT  https://github.com/holochain/holochain-rust/gr...   
3     4. aelf   ELF  https://github.com/aelfProject/AElf/graphs/com...   
4   5. RChain  RHOC  https://github.com/rchain/rchain/graphs/commit...   

  commits     contributors  
0   9,483  24 contributors  
1   7,121  55 contributors  
2   6,458  28 contributors  
3   5,532  26 contributors  
4   5,216  49 contributors

The numbers on the left side of the DataFrame are known as the "index", which act as identifiers for the rows. Because we didn't specify an index, it was automatically assigned as the integers 0 to 115.

We can examine the bottom of the DataFrame using the `tail()` method:

In [193]:
df.tail()

name coin                                                url  \
799    800. Infinipay  IFP  https://github.com/infinipay/infinipay/graphs/...   
800       801. Allion  ALL  https://github.com/EpyxZ/Allion/graphs/commit-...   
801          802. NEM  XEM  https://github.com/NemProject/nem.core/graphs/...   
802  803. Thingschain  TIC  https://github.com/TICnetwork/TIC-token/graphs...   
803       804. X-Coin  XCO  https://github.com/jimblasko/xcoin/graphs/comm...   

    commits    contributors  
799       1                  
800       1   1 contributor  
801       1  4 contributors  
802       1   1 contributor  
803       1  2 contributors

In [233]:
df['commits'].head(1).values

array(['9,483'], dtype=object)

## Exporting the dataset to a CSV file

Finally, we'll use pandas to export the DataFrame to a CSV (comma-separated value) file, which is the simplest and most common way to **store tabular data in a text file:**

In [234]:
df.to_csv('git_activity.csv', index=False, header=False,encoding='utf-8')

We set the `index` parameter to `False` to tell pandas that we don't need it to include the index (the integers 0 to 115) in the CSV file. You should be able to find this file in your working directory, and open it in any text editor or spreadsheet program!

In the future, you can rebuild this DataFrame by reading the CSV file back into pandas:

In [196]:
df = pd.read_csv('git_activity.csv', encoding='utf-8')

If you want to learn a lot more about the pandas library, you can watch my video series, [Easier data analysis in Python with pandas](http://www.dataschool.io/easier-data-analysis-with-pandas/), or check out my [top 8 resources for learning pandas](http://www.dataschool.io/best-python-pandas-resources/).

## Summary: 16 lines of Python code

Here are the 16 lines of code that we used to scrape the web page, extract the relevant data, convert it into a tabular dataset, and export it to a CSV file:

In [10]:
import requests
r = requests.get('https://www.cryptomiso.com/')

from bs4 import BeautifulSoup
soup = BeautifulSoup(r.text, 'html.parser')
results = soup.find_all('h4', class_='card-title')

records = []
for result in results:
    name = result.contents[0].split()[1]
    coin = result.a.text
    url = result.find('small').find('a')['href']
    commits = result.find('span').contents[0].split()[0]
    contributors = result.small.find('span', 'smaller text-muted float-right mt-1').text
##    slogan = result.h6.contents
    records.append((name, coin, url, commits, contributors))

import pandas as pd
df = pd.DataFrame(records, columns=['name', 'coin', 'url', 'commits', 'contributors'])
df.to_csv('git_activity2.csv', index=False, header=False, encoding='utf-8') ## Removing index and header for BigQ

### Upload File to BigQuery

Run the belon in the command line to load file into GCP BigQ. When upload done, data can be queried.

`gcloud auth login`

`bq init`

`cd --filepath`

`bq load --max_bad_records 1 swift-reef-233803:gitactivity.gitactivity git_activity1.csv`

### Getting Annotated Address List (bloxy api)

In [20]:
import requests
url = 'https://bloxy.info/api/address/list_all?limit=10000&key=ACCNJXHGsSRvT&format=csv'
data = requests.get(url)

In [21]:
## Create .csv file from api call. Re: reduce cost from calling API everytime. 
with open('addresses.csv', 'w+') as f:
    f.write(data.text)

In [3]:
## Create dataframe
import pandas as pd
df_address = pd.read_csv('addresses.csv')

In [4]:
df_address.columns

Index(['address', 'smart_contract_type', 'balance', 'address_annotation',
       'transfers_from_count', 'calls_from_count'],
      dtype='object')

In [5]:
# Create sub-selection of columns 
cols = ['address', 'smart_contract_type', 'balance', 'address_annotation']

In [15]:
## Cleaning dataset to get only annotated addresses
sub = df_address[cols].dropna().to_dense() #.to_dense used to ge

In [16]:
len(sub)

250

In [17]:
sub.to_csv('address1.csv', index=False)

### Filtering data with pandas

In [92]:
df_address[df_address['smart_contract_type'] == 'Wallet'].head().dropna()

address smart_contract_type  \
2  0x742d35cc6634c0532925a3b844bc454e4438f44e              Wallet   
3  0x4e9ce36e442e55ecd9025b9a6e0d88485d628a67              Wallet   
8  0xdc76cd25977e0a5ae17155770273ad58648900d3              Wallet   

        balance                                 address_annotation  \
2  2.167089e+06  Bitfinex_5, Exchange Wallet, Exchange, Fiat Ga...   
3  2.152132e+06                       Binance_6, Binance, Exchange   
8  8.508607e+05                           Huobi_6, Exchange Wallet   

   transfers_from_count  calls_from_count  
2                    72               212  
3                     2               154  
8                    31                 0

In [101]:
df_address[(df_address.smart_contract_type == 'Wallet')].head()

address smart_contract_type  \
2  0x742d35cc6634c0532925a3b844bc454e4438f44e              Wallet   
3  0x4e9ce36e442e55ecd9025b9a6e0d88485d628a67              Wallet   
4  0x53d284357ec70ce289d6d64134dfac8e511c8a3d              Wallet   
5  0x66f820a414680b5bcda5eeca5dea238543f42054              Wallet   
8  0xdc76cd25977e0a5ae17155770273ad58648900d3              Wallet   

        balance                                 address_annotation  \
2  2.167089e+06  Bitfinex_5, Exchange Wallet, Exchange, Fiat Ga...   
3  2.152132e+06                       Binance_6, Binance, Exchange   
4  1.378754e+06                                                NaN   
5  1.200002e+06                                                NaN   
8  8.508607e+05                           Huobi_6, Exchange Wallet   

   transfers_from_count  calls_from_count  
2                    72               212  
3                     2               154  
4                     3                 2  
5                     1                18  
8                    31                 0

In [19]:
df_address[(df_address.smart_contract_type in 'Wallet')].head()

TypeError: 'in <string>' requires string as left operand, not Series

In [85]:
df_address['address_annotation'][2].split('_')[0]

'Bitfinex'

## Appendix A: Web scraping advice

- Web scraping works best with **static, well-structured web pages**. Dynamic or interactive content on a web page is often not accessible through the HTML source, which makes scraping it much harder!
- Web scraping is a "fragile" approach for building a dataset. The HTML on a page you are scraping can **change at any time**, which may cause your scraper to stop working.
- If you can **download the data** you need from a website, or if the website provides an **API with data access**, those approaches are preferable to scraping since they are easier to implement and less likely to break.
- If you are **scraping a lot of pages** from the same website (in rapid succession), it's best to insert delays in your code so that you don't overwhelm the website with requests. If the website decides you are causing a problem, they can block your IP address (which may affect everyone in your building!)
- Before scraping a website, you should review its **robots.txt file** (also known as the [Robots exclusion standard](https://en.wikipedia.org/wiki/Robots_exclusion_standard)) to check whether you are "allowed" to scrape their website. (Here is the [robots.txt file for nytimes.com](http://www.nytimes.com/robots.txt).)

## Appendix B: Web scraping resources

- The [Beautiful Soup documentation](http://www.crummy.com/software/BeautifulSoup/bs4/doc/) is written like a tutorial, and is worth reading to gain a detailed understanding of the library.
- For more Beautiful Soup examples, see [Web Scraping 101 with Python](http://www.gregreda.com/2013/03/03/web-scraping-101-with-python/), [More web scraping with Python](http://www.gregreda.com/2013/04/29/more-web-scraping-with-python/), and this [web scraping lesson](http://web.stanford.edu/~zlotnick/TextAsData/Web_Scraping_with_Beautiful_Soup.html) from Stanford's "Text As Data" course.
- [Web Scraping with Python](https://www.youtube.com/watch?v=p1iX0uxM1w8) is a 3-hour video tutorial covering Beautiful Soup and other scraping tools. (The [slides](https://docs.google.com/presentation/d/1uHM_esB13VuSf7O1ScGueisnrtu-6usGFD3fs4z5YCE/edit#slide=id.p) and [code](https://github.com/kjam/python-web-scraping-tutorial) are also available.)
- [Scrapy](http://scrapy.org/) is a popular application framework that is useful for more complex web scraping projects.
- [How a Math Genius Hacked OkCupid to Find True Love](http://www.wired.com/2014/01/how-to-hack-okcupid/all/) and [How Netflix Reverse Engineered Hollywood](http://www.theatlantic.com/technology/archive/2014/01/how-netflix-reverse-engineered-hollywood/282679/?single_page=true) are two fun examples of using web scraping to build an interesting dataset.

## Appendix C: Alternative syntax for Beautiful Soup

It's worth noting that Beautiful Soup actually offers multiple ways to express the same command. I tend to use the most verbose option, since I think it makes the code readable, but it's useful to be able to recognize the alternative syntax since you might see it used elsewhere.

For example, you can **search for a tag** by accessing it like an attribute:

In [34]:
# search for a tag by name
first_result.find('strong')

# shorter alternative: access it like an attribute
first_result.strong

<strong>Jan. 21 </strong>

You can also **search for multiple tags** a few different ways:

In [35]:
# search for multiple tags by name and attribute
results = soup.find_all('span', attrs={'class':'short-desc'})

# shorter alternative: if you don't specify a method, it's assumed to be find_all()
results = soup('span', attrs={'class':'short-desc'})

# even shorter alternative: you can specify the attribute as if it's a parameter
results = soup('span', class_='short-desc')

For more details, check out the [Beautiful Soup documentation](https://www.crummy.com/software/BeautifulSoup/bs4/doc/).